## TP RES203 Caching: Part 2, evaluate cache hit ratio


While the user experience resulting from deployment of caches depends on the application at hand (e.g., are caches deployed to reduce delay and increase interactivity? or increase throughput and so the video quality? or to reduce video stuttering? etc.)  performance of a caching system are typically described by means of the cache hit ratio (denoted $P_{hit}$ or simply $h$).

Simply put, the cache _hit_ ratio is the fraction of requests that can be served by the cache. The complementary fraction,  $1-P_{hit}$, is called the cache _miss_ ratio. The cache hit ratio is the result of multiple factors interplaying with each other, notably:
* The request arrival process 
* The catalog of possible requests, and their relative  popularity distribution
* The cache size, acceptance and replacement policies
* The routing policy in a cache hierarchy, in case of complex topologies

To make it very simple, in this TP we will consider:
* A simple arrival arrival process, called Independent Reference Model (IRM) where requests are independent of each other, and arrive with a Poisson process of rate $\Lambda$
* A catalog  comprising $M$ distinct objects, with $M$ large, whose popularity is Zipf-distributed
* A cache of size $C$ objects, with $C<<M$, that accept every object and replaces the old one with either a Least Frequently Used (LFU) or Least Recently Used (LRU) policies
* A simple topology consisting of a single cache.

Hints toward more realistic (and thus complex) systems are given in Part 4 of this TP.


In [ ]:
#%matplotlib notebook

from ipywidgets import interact, interactive, fixed, interact_manual, IntSlider
from IPython.display import clear_output, display, HTML

import math
import numpy as np
import timeit

from scipy import integrate
from scipy.optimize import fsolve

from matplotlib import pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib.colors import cnames
from matplotlib import animation

from itertools import takewhile

from __future__ import division

## Zipf popularity distribution
    
Requests for digital objects have a skewed popularity: i.e., there are few very popular objects (the last video of a popular singer on YouTube) and a lot of unpopular ones (the numerous reprises of the very same song by amateur fans without artistic skills and that sing out of tune). Also domain names follow the same skew: there are very popular Websites that everybody connects to, and a very long tail of unpopular websites that are seldom visited.

Zipf law (along with  Weibull and Mandelbrot-Zipf) well describes such popularity skew. In particular,     In particular, denoting with $M$ the _catalog cardinality_, and with $1 \le i \le M$ the rank of the $i$-th most popular content, the probability of requesting the content with rank $i$ is expressed as:

\begin{equation} 
P(X=i)=\frac{i^{-\alpha}}{ \sum_{j=1}^M{j^{-\alpha}} }.
\end{equation} 
where $\alpha > 0$ is the skew of the distribution.   

In particular, observe that
*  $\sum_{j=1}^M{j^{-\alpha}}$ is a normalization factor so that $\sum_{j=1}^M P(X=i) = 1$. 
*  $P(X=i)/P(X=1) =  i^{-\alpha} / 1^{-\alpha} = i^{-\alpha}$, i.e., the i-th object is  $i^{\alpha}$ times less popular than the most popular object in the catalog
*  Quantiles of the Zipf law exhibit a sharp phase transition as a function of $\alpha$.

Clearly,  the value of the Zipf exponent $\alpha$ plays a paramount role in determining the caching performance; indeed, the percentage of requests directed to the $C$ most popular contents, i.e., $P(C)=\sum_{i=1}^C{P(X=i)}$, heavily varies with $\alpha$.  The size of the catalog plays a role as well, as it affects the normalization constant in  $ \sum_{j=1}^M{j^{-\alpha}}$. While there is no agreement on what exactly is the value of $\alpha$, there is a general agreement on the size of catalogs now exceeds billion $M=10^9$ items (and sometimes trillion $M=10^{12}$ items).


Considering that 10 years ago YouTube was reported to have in excess of 100,000,000 videos and that it was reported that 10 years ago more than 500,000,000 DNS sub-domains were registered under the .com TLD, it seems that we should at least aim at $M=10^8$. 



**Your assignment is to evaluate the fraction of requests that are directed to the first most popular $C=1000$ objects out of a catalog of $M=10$ items as a function of $\alpha$**

Notice that the code below allocates the full vector of  $M$ elements. This is convenient but can be slow, especially on slow machines (e.g., C126). Rewrite it to smoothly handle the case of larger catalogs.


In [ ]:
    M=1e6
    C=1e3
    alpha=np.linspace(0.6, 1.4, num=10) 
    perc=[]
    for A in alpha:
        pdf = np.arange(1.0, M + 1.0) ** -A
        pdf /= np.sum(pdf)
        #perc.append(np.percentile(pdf,95))
        perc.append(sum(pdf[:int(C)]))
    
    plt.figure()
    plt.plot(alpha, perc)
    plt.show()

## LFU Replacement Policy
Since caches have a limited amount of space to store contents (which we suppose being equal to $C$ contents), we need a _replacement policy_ to decide which content needs to be evicted when the cache is full and a new content needs to be stored. Among several techniques, a very popular and useful one is represented by the _Least Frequently Used_ (LFU).

In its classic implementation, an LFU cache keeps track of the access frequency by assigning a counter to each stored content, and evicting the one with the lowest counter when the cache is full. However, if the content popularity is known a priori, a LFU cache can be implemented by statically storing the $C$ most popular contents, thus providing optimal performance under IRM. 

LFU is discouraged in real contexts with evolving popularity, since learning the popularity takes time (e.g., newly cached items with low counters might be soon evicted even though they might be required frequently thereafter) and the LFU policy is thus slow to adapt to changes.  However, in cases of stationary popularity and IRM content,  LFU gives an upper-bound of the cache hit ratio, since the content is placed a priori in the cache so that popular content does not even yield a miss for its first request which is unrealistic (remember the cache warmup in the Phase 1 of this TP).

Thus, from our perspective LFU is a very simple and insightful policy worth investigating.
.   



**Your second assignment is to evaluate the hit ratio of an LFU cache of size $C$, for a catalog of $M$ items with Zipf popularity of skew $\alpha$**



In [ ]:
def solve_lfu(M=1e7, C=1e3, A=1.0, verbose=True):  
    """ 
    Compute LFU cache hit ratio
    """
    print("solve_lfu(%g,%s,%s)" % (M,C,A))
    start_time = timeit.default_timer()

    # does this code sound familiar? see previous cell
    pdf = np.arange(1.0, M + 1.0) ** -A
    pdf /= np.sum(pdf)
    hit = sum(pdf[:int(C)])
    
    if verbose:
        print ("\telapsed= %.2f sec" % (timeit.default_timer() - start_time ))
        print ("\tlfu_hit= %.2f " % (hit))
    return hit

In [ ]:
""" 
You can now use the solve_lfu() function to assess the cache hit probability for varying \alpha
"""
    
#hit_lfu=[lambda x: solve_lfu(M=1e7,C=1e3,A=x) for x in alpha]
alpha=np.linspace(0.6, 1.4, num=10)
hit_lfu=[]
plt.figure()
for a in alpha:
    hit_lfu.append(solve_lfu(M=1e7,C=1e3,A=a,verbose=False))
plt.plot(alpha,hit_lfu)
plt.show()

While LFU is very simple to compute numerically, it is also very simple to approximate in close form.
Particularly, for $\alpha=1$ we can  approximate the harmonic numbers $H_M$ and $H_C$ with the 
logarithm log(M) and log(C), neglecting the Eulerm-Mascheroni constant. While the approximation is crude, it is quite accurate especially for very large catalogs -- which is the interesting regime for the Internet.
Since the approximation is available in closed-form, it is istantaneous to compute -- which is very useful for Internet-size catalogs.

Compare the exact and approximate LFU solutions. Notice that for large catalog sizes, Jupyter notebook can use **all the RAM memory** of the PC and start swapping (i.e., using the virtual memory on the hard disk) which makes computation very slow (CPU goes to few percentage as the time is spent in swapping from/to disk) and that can addtionally hang your PC.

**Your third assignment is to approximate the hit ratio of an LFU cache of size  $C$ , for a catalog of  $M\in\{10^6,10^7,10^8,10^9,10^{10},10^{11},10^{12}\}$  items with Zipf popularity of skew  $\alpha=1$** 





In [ ]:
## LFU cache hit ratio -- Aproximate solution
def solve_lfu_approx(M=1e7, C=1e3, A=1.0, verbose=True):
    """ 
    Compute LFU cache hit ratio approximating harmonic numbers  
    H_M and H_C with a logarithm log(M) and log(C) ignoring the
    Euler-Mascheroni constant which is o(1). The approximation
    is accurate as M gets latrge
    """
    print("solve_lfu_approx(%g,%s,%s)" % (M,C,A))
    if A == 1:
        h =  np.log(C) / np.log(M)
        if verbose:
            print ("\tlfu_hit= %.2f " % (h))
        return h
    else:
        return -1
    
def solve_lfu_slow(M=1e7, C=1e3, A=1.0, verbose=True):  
    """ 
    Compute the exact LFU cache hit ratio in the simplest way. 
    It is slow for small catalogs M but scales well in memory
    for large M (unlike solve_lfu that can make your machine swap)
    """
    print("solve_lfu_slow(%g,%s,%s)" % (M,C,A))
    start_time = timeit.default_timer()

    sumM = sumC = 0
    #in 2.6 xrange was an iterator and range not
    #in 3.x xrange does not exist and range is an iterator
    # for m in range(1,M+1):
    #better be safe and do a C-style while loop
    m=1
    while m<=M+1:
        sumM += m**-A
        if m==C:
            sumC=sumM
        m += 1   
    hit = sumC/sumM
    
    if verbose:
        print ("\telapsed= %.2f sec" % (timeit.default_timer() - start_time ))
        print ("\tlfu_hit= %.2f " % (hit))
    return hit    



In [ ]:
#for small catalogs, solve_lfu is efficient 
catalog=[1e6, 1e7]
for M in catalog:
    solve_lfu(M,C=1e3,A=1.0)
    solve_lfu_slow(M,C=1e3,A=1.0)
    solve_lfu_approx(M,C=1e3,A=1.0)


#for large catalogs, solve_lfu can hang your notebook
catalog=[1e8, 1e9]
for M in catalog:
    #use solve_lfu at your own risk.
    solve_lfu_slow(M,C=1e3,A=1.0)
    solve_lfu_approx(M,C=1e3,A=1.0)
  
    
#for very large catalogs, the approximation gets more accurate and
# since it is also significantly faster, it is OK for a first estimation
cache=[1e3, 1e4, 1e5]
catalog=[1e6, 1e7, 1e8, 1e9, 1e10, 1e11, 1e12]
plt.figure()        
for C in cache:
    hit_lfu_approx = []
    for M in catalog:
         hit_lfu_approx.append(solve_lfu_approx(M,C,A=1.0,verbose=False))
    plt.semilogx(catalog, hit_lfu_approx)

plt.show()

## LRU Replacement policy


As previously introduced, LFU provides an optimistic upper bound of cache hit performance for stationary catalogs, and is unsuitable since it slowly learn the request frequency for dynamic catalogs.

A good alternative to LFU is provided by  the _Least Recently Used_ (LRU) policy, that
in case the cache is full and a new content needs to be inserted, it evicts the content that has not been requested for the longest time. Ideally, you can imagine that each time a cached content is requested, its timer is updated; on eviction, the content corresponding to the oldest timer is selected.  In practice, LRU is implemented by moving contents to the head each time they are requested, so that older contents move toward the tail.
 
A LRU cache provides the best compromise between performance and easy implementation, and is thus very popular, which makes another goot candidate to study for this TP. In the following, we use a very simple yet accurate model for the evaluation of the LRU cache hit rate, that is known as the "Che approximation".

**Your fourth assignment is to compare the hit ratio of an LRU vs a LFU caches of size  $C$ , for a catalog of  $M\in\{10^7,10^8\}$  items with Zipf popularity of skew  $\alpha=1$** 

You can of course try bigger size catalogs, although the solution takes more time. The important point here is the _relative_ comparison of practical (LRU) vs ideal (LFU) performance, so that you know the error you make when estimating the hit ratio with a simple LFU formula as a first crude approximation for system design.


In [ ]:
def solve_lru_che(M=1e7, C=1000, A=1, verbose=True):  
    """ 
    Compute the LRU cache hit ratio with the Che approximation
    """ 
    print("solve_lru_che(%g,%s,%s)" % (M,C,A))
    start_time = timeit.default_timer()
               
    pdf = np.arange(1.0, M + 1.0) ** -A
    pdf /= np.sum(pdf)
    contents = range(len(pdf)) 

    def tc_equation(T_C):
        return sum(math.exp(-pdf[j] * T_C) for j in range(len(pdf))) \
            - len(pdf) + C
    
    #Che approximation: consider the random variable of 
    #mean value E[T_C] equal to a constant of value T_C
    T_C = fsolve(tc_equation, x0=C)[0]        
    h_c = [1 - math.exp(-pdf[i] * T_C) for i in contents]
    hit = sum(pdf[i] * h_c[i] for i in range(len(pdf)))
               
    elapsed = timeit.default_timer() - start_time    
    if verbose:
        print ("\tTC = %.2f" % T_C)
        print ("\telapsed= %.2f sec" % (timeit.default_timer() - start_time ))
        print ("\tlru_hit= %.2f " % (hit))           
    return hit           


In [ ]:
M=1e7
solve_lfu(M,C=1e3,A=1.0)
solve_lfu_approx(M,C=1e3,A=1.0)
solve_lru_che(M,C=1e3,A=1.0)